In [1]:
import sys
# sys.path.append("../")
import os
os.chdir("../")

In [2]:
import os
dataPath="data/msmarco/embStats"
arr = os.listdir(dataPath)

In [4]:
import glob

In [6]:
dataPath

'data/msmarco/embStats'

In [10]:
import os
import re

def glob_re(pattern, strings):
    return filter(re.compile(pattern).match, strings)

In [27]:
glob.glob(f"data/msmarco/embStats/bkkemb_CorpusStats.pkl_*")

['data/msmarco/embStats/bkkemb_CorpusStats.pkl_1000000']

In [20]:
txtfiles = []
for file in glob.glob(f"{dataPath}.pkl_*"):
    txtfiles.append(file)

In [21]:
txtfiles

[]

In [16]:
 os.listdir(dataPath)

['QueryStats.pkl',
 'bkemb_CorpusStats.pkl',
 'bkkemb_CorpusStats.pkl_1000000',
 'emb_QueryStats.pkl',
 'emb_query.pkl']

In [17]:
filenames = glob_re(r'.pkl_', os.listdir(dataPath))

In [19]:
print(filenames)

['QueryStats.pkl', 'bkemb_CorpusStats.pkl', 'bkkemb_CorpusStats.pkl', 'emb_QueryStats.pkl', 'emb_query.pkl']


In [2]:
import torch
from transformers import AutoModelForMaskedLM, AutoTokenizer
from splade.models.transformer_rep import Splade
from splade.utils.utils import restore_model

In [3]:
%load_ext autoreload
%autoreload 2

In [4]:
model_type_or_dir = "experiments/PretrainedModel/splade_distil_CoCodenser_medium/"
# /home/taoyang/research/research_everyday/projects/DR/splade/splade/experiments/toyContrast/AQWPsuedotoy/checkpoint/model_ckpt
# /home/collab/u1368791/largefiles/TaoFiles/splade/experiments/cocondenser_ensemble_distil/checkpoint/model
model = Splade(model_type_or_dir, agg="max")

In [5]:
def get_initialize_config(exp_dict=None, train=False):
    # delay import to reduce dependencies
    # from ..utils.hydra import hydra_chdir
    # hydra_chdir(exp_dict)
    # exp_dict["init_dict"]["fp16"] = exp_dict["config"].get("fp16", False)
    config = exp_dict["config"]
    init_dict = exp_dict["init_dict"]
    # if train:
    #     os.makedirs(exp_dict.config.checkpoint_dir, exist_ok=True)
    #     OmegaConf.save(config=exp_dict, f=os.path.join(exp_dict.config.checkpoint_dir, "config.yaml"))
    model_training_config = None
    # else:
    #     if config.pretrained_no_yamlconfig:
    #         model_training_config = config
    #     else:
    #         model_training_config = OmegaConf.load(os.path.join(config["checkpoint_dir"], "config.yaml"))["config"]
    return exp_dict, config, init_dict, model_training_config

In [6]:
# # Program to convert yaml file to dictionary
import yaml
# opening a file
yamlFile="/home/taoyang/research/research_everyday/projects/DR/splade/splade/experiments/debug/checkpoint/config.yaml"
with open(yamlFile, 'r') as stream:
    # try:
    # Converts yaml document to python object
    exp_dictOrig=yaml.safe_load(stream)
# exp_dictOrig=Namespace(exp_dictOrig)
exp_dict, config, init_dict, model_training_config = get_initialize_config(exp_dictOrig)

In [7]:
from splade.utils.utils import makedir, to_list
from tqdm.auto import tqdm
from collections import defaultdict

In [23]:
from splade.index import SparseIndexing,CollectionDatasetPreLoad,CollectionDataLoader
import pickle
class SparseEmbedding(SparseIndexing):
    def __init__(self,*param,**kwparam):
        super().__init__(*param,**kwparam)   
    def emb(self, collection_loader,storePath, id_dict=None):
        doc_ids = []
        embDoc={}
        if self.compute_stats:
            stats = defaultdict(float)
        count = 0
        with torch.no_grad():
            for t, batch in enumerate(tqdm(collection_loader,desc="indexing")):
                inputs = {k: v.to(self.device) for k, v in batch.items() if k not in {"id"}}
                if self.is_query:
                    batch_documents = self.model(q_kwargs=inputs)["q_rep"]
                else:
                    batch_documents = self.model(d_kwargs=inputs)["d_rep"]
                if self.compute_stats:
                    stats["L0_d"] += self.l0(batch_documents).item()
                row, col = torch.nonzero(batch_documents, as_tuple=True)

                data = batch_documents[row, col].cpu().numpy()
                row=to_list(row)
                col=to_list(col)
                # row = row + count
                print(batch["id"])
                batch_ids = to_list(batch["id"])
                print(batch_ids)
                if id_dict:
                    batch_ids = [id_dict[x] for x in batch_ids]
                # print(row)
                for rowCur in row:
                    embDoc[str(batch_ids[rowCur])]=defaultdict(float)
                for ind,(rowCur,colCur) in enumerate(zip(row, col)):
                    embDoc[str(batch_ids[rowCur])][colCur]=data[ind]
        with open(storePath, 'wb') as f:
            pickle.dump(embDoc, f)
        return embDoc
                    
                
        

In [9]:
model_training_config={}
model_training_config["tokenizer_type"]="experiments/PretrainedModel/splade_distil_CoCodenser_medium"
model_training_config["max_length"]=96

In [10]:
config["pretrained_no_yamlconfig"]=True

In [28]:
exp_dict["data"]["COLLECTION_PATH"]

'data/toy_data20/full_collection'

In [24]:
d_collection = CollectionDatasetPreLoad(data_dir=exp_dict["data"]["COLLECTION_PATH"], id_style="row_id")
d_loader = CollectionDataLoader(dataset=d_collection, tokenizer_type=model_training_config["tokenizer_type"],
                                max_length=model_training_config["max_length"],
                                batch_size=config["index_retrieve_batch_size"],
                                shuffle=False, num_workers=10, prefetch_factor=4)


Preloading dataset


0it [00:00, ?it/s]

In [25]:
evaluator = SparseEmbedding(model=model, config=config, compute_stats=True)

avalialbe devices is cuda, count of devices is 4
 --- use 4 GPUs --- 
initializing new index...


In [26]:
embDoc=evaluator.emb(d_loader,storePath="output/emb.pkl")

indexing:   0%|          | 0/126 [00:01<?, ?it/s]

tensor([6021125,  557061,  557063,  557064,  557065, 2293772,  557068,  557070,
        2580496, 6770159, 6127650, 1663013, 1146923, 1146924, 1146925, 1146926,
        5365812, 5455925, 1949754, 1949757, 1441855, 4546624, 1851457, 1851456,
        2113603, 4546627, 3915846, 5759052, 3997774, 8110158,  991318, 2998359])
[6021125, 557061, 557063, 557064, 557065, 2293772, 557068, 557070, 2580496, 6770159, 6127650, 1663013, 1146923, 1146924, 1146925, 1146926, 5365812, 5455925, 1949754, 1949757, 1441855, 4546624, 1851457, 1851456, 2113603, 4546627, 3915846, 5759052, 3997774, 8110158, 991318, 2998359]
tensor([2826326, 3313453, 6127714,  188519, 7479400, 4169833, 1892460, 4505709,
         655475, 6561907,  655477,  589942, 6561911, 4309112, 6561910, 4309114,
        4309115, 4309116, 5742714, 4268158, 5742717,  721024, 5742715, 4112509,
        3252355,  721028,  721029,  721030, 3252357, 1646728, 5873808, 3899536])
[2826326, 3313453, 6127714, 188519, 7479400, 4169833, 1892460, 4505709, 6554

In [27]:
embDoc

{'6021125': defaultdict(float,
             {1016: 0.19942702,
              1037: 0.0029254043,
              1038: 0.44127455,
              1039: 0.8517522,
              1057: 0.103796795,
              1997: 0.17513433,
              1999: 0.06062462,
              2000: 0.19942702,
              2022: 0.51860774,
              2025: 0.38905516,
              2036: 0.061543316,
              2060: 0.39235875,
              2079: 0.26969907,
              2089: 0.2947372,
              2104: 0.67640626,
              2149: 0.2293741,
              2193: 0.33675122,
              2349: 0.1535925,
              2375: 0.47097972,
              2421: 0.57676697,
              2442: 0.008750663,
              2457: 0.32411948,
              2501: 1.2937635,
              2553: 0.20898125,
              2583: 0.12814583,
              2590: 0.6563454,
              2592: 0.018384648,
              2636: 0.7047978,
              2640: 0.049533933,
              2649: 0.9606066,
          

In [ ]:
# import pickle 
# storePath="../data/msmarco/embStats"
# with open(storePath, 'rb') as f:
#             embDoc = pickle.load(f)